In [248]:
from yelpapi import YelpAPI

In [249]:
import pandas as pd
import requests
import json
from config import API_Key 
# from config import bea_api

In [250]:
from pprint import pprint

In [251]:
yelp_api = YelpAPI(API_Key)

In [91]:
bea_url = 'https://apps.bea.gov/api/data'
bea_api = '0BEDA572-87F5-46AB-8614-4949AE2FE5B8'


In [11]:
bea_final_url = f'{bea_url}?&UserID={bea_api}&method=GetData&Datasetname=Regional&TableName=CAINC1&LineCode=3&GeoFIPS=COUNTY&Year=2014&ResultFormat=JSON'

In [6]:
bea_list_url=f'https://apps.bea.gov/api/data?&UserID={bea_api}&method=GETDATASETLIST&'

In [7]:
bea_list = requests.get(bea_list_url).json()

In [92]:
bea_data = requests.get(bea_final_url).json()

In [93]:
data = bea_data['BEAAPI']['Results']['Data']

In [94]:
PCI = pd.DataFrame(data)

In [96]:
PCI.drop(['Code', 'GeoFips', 'CL_UNIT', 'UNIT_MULT', 'NoteRef'], axis = 1, inplace=True)

In [97]:
PCI.to_csv("PCI.csv")

In [24]:
PCI = pd.read_csv('PCI.csv')

In [25]:
PCI.loc[PCI['GeoName'] == 'Denver, CO']

Unnamed: 0     GeoName  TimePeriod DataValue
284         284  Denver, CO        2014    68,046

In [26]:
pop_html = pd.read_html('https://en.wikipedia.org/wiki/List_of_United_States_cities_by_population')

In [27]:
pop_db = pop_html[4]

In [28]:
pop_db.drop(['Location', '2016 population density', '2016 population density.1', '2018rank'], axis = 1, inplace=True)

In [29]:
pop_db = pop_db.rename(columns={'State[c]':'State'})

In [30]:
x = 'New York'

In [31]:
x.partition('[')

('New York', '', '')

In [32]:
pop_db['City'] = pop_db['City'].apply(lambda x: x.partition('[')[0])

In [33]:
pop_db.to_csv('pop_db.csv')

In [156]:
PCI['GeoName'].p

0          Autauga, AL
1          Baldwin, AL
2          Barbour, AL
3             Bibb, AL
4           Blount, AL
             ...      
3133    Sweetwater, WY
3134         Teton, WY
3135         Uinta, WY
3136      Washakie, WY
3137        Weston, WY
Name: GeoName, Length: 3138, dtype: object

In [35]:
x = PCI['GeoName'][0]

In [36]:
x.partition(',')[0]


'Autauga'

In [37]:
PCI['City'] = PCI['GeoName'].apply(lambda x: x.partition(',')[0])
PCI['State'] = PCI['GeoName'].apply(lambda x: x.partition(',')[2])


In [38]:
PCI.drop(['GeoName', 'TimePeriod'], axis=1, inplace=True)

In [40]:
st_abbr = pd.read_csv('st_abbr.csv')

In [41]:
st_abbr.drop(['Abbrev'], axis=1, inplace=True)

In [42]:
population = st_abbr.merge(pop_db, on='State')

In [43]:
population.drop(['State'], axis=1, inplace=True)

In [44]:
population = population.rename(columns={'Code':'State'})

In [46]:
final_db = population.merge(PCI, on='City')

In [48]:
#delete empty spaces before and after State abbr
PCI['State'] = PCI['State'].apply(lambda x: x.strip())

In [50]:
final_db = population.merge(PCI, on=['City', 'State'])

In [53]:
final_db.to_csv('merged_data.csv')

In [5]:
final_db = pd.read_csv("merged_data.csv")

In [34]:
yelp_list_st = []
yelp_list_city = []
for row in final_db.iterrows():
    yelp_list_city.append(row[1][2])
    yelp_list_st.append(row[1][1])

# results_mexi = yelp_api.search_query(term='massage', location='denver, co')

In [8]:
terms = ['spas', 'privateschools', 'restaurants']
terms[0]

'spas'

In [247]:
import time 

In [ ]:
for i in range(0,19):
    if i == 0:
        offset = 0
    else: 
        offset = offset + 50
    print(offset)

In [120]:
x = round(test['total']/50)
x

2

In [258]:
results = yelp_api.search_query(term='spa', location='tuscaloosa, al')
print(results['total'])
for rest in results['businesses']:
    print(rest['name'])

48
Spa Belle La Vie
Nancy Taylor Skin Therapy & Day Spa
Chancee's Wellness Spa
Hydralive Therapy
Gilda's Salon & Day Spa
Tuscaloosa MedSpa
Professional Massage Therapy
Massaged Life & Wellness Academy
Nova Vita Massage Therapy Clinic
Relax Magic
Bellagio Nails Spa
B.A.B.Y. Nail Spa
Happiness Nails & Spa
A Grayceful Touch Massage
The Recovery Room - Cryo RTR and JW OMT
Dustin Wright
Glam Salon & Blow Dry Bar
Image Makers
New Creations Salon
Salon Serenity


In [155]:
try: 
    ag
    print('try')
except:
    ag= {}
    print('except')
    
finally:
    print('finally')

SyntaxError: 'break' outside loop (<ipython-input-155-f2d354a608a2>, line 10)

In [259]:
#loop through results and create dataframe for desired info
# def test(location, terms):
#     print(location , terms)

def getresults(location, terms):
    
    time.sleep(2)
    name = []
    cat = []
    price = []
    rating = []
    review = []
    state = []
    city = []
    bus_Type = []
    
    try:
        results = yelp_api.search_query(term=terms, location=location)
        time.sleep(1)
    except: 
        print(f'no listing for {location} and {terms}')
        dict1 = {}
        return dict1
     
    #loop through creating offsets of 50 for each request     
    offset = 0
    if results['total'] > 1000:
        x = 20
    else:
        x = round(results['total']/50) #calculate how many offset calls to make
    
    for i in range(0,x):
        if i == 0:
            offset = 0
        else: 
            offset = offset + 50 #increase each offset by 50 for each iteration
        
        try:
            results = yelp_api.search_query(term=terms, location=location, offset=offset) 
            time.sleep(1)
            
            #get results and append to list
            for rest in results['businesses']:
                name.append(rest['name'])
                cat.append(rest['categories'][0]['title'])
                state.append(location.split(',')[1])
                city.append(location.split(',')[0])
                bus_Type.append(terms)

                try:
                    price.append(f"{rest['price']}")
                except: 
                    price.append('0')
                try:
                    rating.append(rest['rating'])
                except: 
                    rating.append('0')  
                try:                
                    review.append(rest['review_count'])
                except:
                    review.append('0')
            
            
            dict1 = {'State': state,
                'City': city,
                'name': name,
                'cat': cat,
                'price': price,
                'rating': rating, 
                'review': review,
                'BusinessType':bus_type}
                                 
        except: 
            print(f'error reached at {location} and {terms} offset {offset}')
            try: 
                dict1
            except:
                dict1 = {}
            finally:
                return dict1
    try:                             
        return dict1                        
    except UnboundLocalError:
        dict1={}
        return dict1

In [ ]:
terms

In [171]:
resulttest = []

test_city = ['tuscaloosa, al']
test_term = ['spa']
for x in range(0, len(test_term)):
    for i in range(0, len(test_city)):
        result = getresults(test_city[i], test_term[x])
        resulttest.append(result)
        

In [ ]:
#main loop to call query function
resultx = []
for x in range(0, len(terms)):
    for i in range(0, len(yelp_list_ab)):
        location = f'{yelp_list_city[i].lower()}, {yelp_list_st[i].lower()}'
        result = getresults(location, terms[x])
        resultx.append(result)
        
        

error reached at montgomery, al and spas offset 0
error reached at mobile, al and spas offset 0
error reached at tuscaloosa, al and spas offset 0
error reached at los angeles, ca and spas offset 0
error reached at san diego, ca and spas offset 0


In [105]:
new_list=['worcester, ma']

True

In [121]:
#loop and query 
resulty = []
result = []
new_city_list = yelp_list_city[26:49]
new_state_list = yelp_list_st[26:49]
for i in range(0, len(new_city_list)):
    location = f'{new_city_list[i].lower()}, {new_state_list[i].lower()}'
    result = getresults(location, 'spa')
    print('success')
    resulty.append(result)

error reached at worcester, ma and spa
success
success
success
error reached at st. louis, mo and spa
success
success
error reached at new york, ny and spa
success
error reached at durham, nc and spa
success
success
error reached at philadelphia, pa and spa
success
error reached at providence, ri and spa
success
success
no listing for houston, tx and spa
success
no listing for dallas, tx and spa
success
no listing for austin, tx and spa
success
error reached at el paso, tx and spa
success
success
error reached at midland, tx and spa
success
no listing for denton, tx and spa
success
no listing for tyler, tx and spa
success
error reached at richmond, va and spa
success
no listing for spokane, wa and spa
success
no listing for milwaukee, wi and spa
success
success


In [167]:
b = pd.DataFrame(resultx[0])
for i in range(1, len(resultx)):
    try:
        c = pd.DataFrame(resultx[i])
        b = b.append(c)
    except ValueError:
        print(f'error at {i}')

error at 143


In [168]:
b

State City                                               name  \
0        montgomery   al                                           Spa Elia   
1        montgomery   al                                      Pearl Massage   
2        montgomery   al                    Sophia European Day Spa & Salon   
3        montgomery   al                                   Hands On Healing   
4        montgomery   al      Natural Healing Acupressure & Massage Therapy   
5        montgomery   al                         Total Freedom Wellness Spa   
6        montgomery   al                    Lake George Massage and Day Spa   
7        montgomery   al                             Indulgence Salon & Spa   
8        montgomery   al                              Amplify Salon and Spa   
9        montgomery   al                                    Midtown Massage   
10       montgomery   al                                      Sunny Massage   
11       montgomery   al                                   Vital Beauty Bar   
12       montgomery   al                           Massage Envy - Eastchase   
13       montgomery   al                         Smart Skin Med Spa & Salon   
14       montgomery   al                           Nails, Lash, & Threading   
15       montgomery   al                                              Bella   
16       montgomery   al                              Gwen's A Southern Spa   
17       montgomery   al                         Pink and White Nail Lounge   
18       montgomery   al                           Mind & Body Holistic Spa   
19       montgomery   al                          Debbie Russell Aesthetics   
20       montgomery   al                                  Kimistry Hair Lab   
21       montgomery   al                                         SmartStyle   
22       montgomery   al                                          L A Nails   
23       montgomery   al                                   Lu's Acupressure   
24       montgomery   al                                         Lisa Nails   
25       montgomery   al                               Beauty Nails and Spa   
26       montgomery   al                                  Wow Salon and Spa   
27       montgomery   al                                 Shayla Nails & Spa   
28       montgomery   al                          Baynes-A European Day Spa   
29       montgomery   al                                        Gloria Nail   
30       montgomery   al                                   WM William Mason   
31       montgomery   al                                Hughes Pools & Spas   
32       montgomery   al                                 Doug's 2 Salon-Spa   
33       montgomery   al                                        Nail Studio   
34       montgomery   al                               Taylor Touch Therapy   
35       montgomery   al                                  Fancy Nails & Spa   
36       montgomery   al                                           Salon H3   
37       montgomery   al                                 Nails by Elizabeth   
38       montgomery   al                                   Number One Nails   
39       montgomery   al                                       Galaxy Nails   
0            mobile   al                          Elements Massage - Mobile   
1            mobile   al                         Mountain Massage & Day Spa   
2            mobile   al                                           Spa Blue   
3            mobile   al                              Bliss Salon & Day Spa   
4            mobile   al                                  Delatorre Day Spa   
5            mobile   al                                 Nouveau On Dauphin   
6            mobile   al                                   Massage Wellness   
7            mobile   al                                       Harlow Salon   
8            mobile   al                                         Spa Tea Da   
9            mobile   al                    pure life massage an

In [27]:
b = pd.DataFrame(resultx[0])
for i in range(1, len(resultx)):
    c = pd.DataFrame(resultx[i])
    b = b.append(c)

In [61]:
b.loc[b['name'] == 'La Peau Spa']

State City         name        cat price  rating  review
0  fresno   ca  La Peau Spa  Skin Care    $$     5.0     144

In [173]:
b.to_csv('bigdata.csv')

In [175]:
b = b.reset_index(drop=True)

In [242]:
pd.set_option('max_rows', 100)


In [177]:
b = b.rename(columns={'State':'City', 'City':'State'})

In [184]:
City_list = b['City'].unique()

In [239]:
d = b.sample(frac=.1)
 

In [230]:
d['price'] = d['price'].apply(lambda x: 1 if (x == '$')

SyntaxError: unexpected EOF while parsing (<ipython-input-230-5f68e229daad>, line 1)

In [241]:
d['price']=d['price'].apply(lambda x: 1 if (x == "$") else x)
d['price']=d['price'].apply(lambda x: 2 if (x == "$$") else x)
d['price']=d['price'].apply(lambda x: 3 if (x == "$$$") else x)
d['price']==d['price'].apply(lambda x: 4 if (x == "$$$$") else x)

12668     $$
11959      $
11526      0
6584      $$
1096      $$
12709      $
7195      $$
13766     $$
14030      $
203        0
14414      $
164        0
8135       $
2349      $$
7605       $
10648      $
11911      $
9673       $
118       $$
4636       0
8595      $$
2502       0
11993      $
5227       0
11227     $$
6929       0
4747       0
12137      $
6868       $
6290      $$
9661      $$
13283      0
8121      $$
7824       0
12878     $$
3294      $$
2831       0
2568      $$
5407      $$
8477       $
13610      $
9383      $$
5393       0
1061     $$$
6834       0
8036      $$
8880      $$
12288      0
3369       0
3285      $$
5177      $$
4803       0
10064     $$
11439      0
1867       0
10422     $$
13597      $
1936      $$
7698       0
5078       $
13420      0
5379       0
14024      0
8415      $$
4911     $$$
14327      $
10114     $$
17        $$
9013      $$
7099       0
12011      $
2898       0
12070      $
12304      0
6077      $$
2329      $$
10626     $$

In [196]:
for p in d['price']:
    if p == "$":
        p = 1
    